## Adding cross reference emails id

In [15]:
from emailProcessor import add_cross_references_emailIds

input_file = "output_data/chat_llm_output_v2.jsonl"
output_file = "output_data/json_with_crossRefs.jsonl"

data, crossRefIds = add_cross_references_emailIds(input_file,output_file, 0.25)

Extracted 649 items with email bodies
Skipped 3 items without bodies: ['mrwf0232', 'xxpw0232', 'nynw0232']

Cross-references added to 649 items!


## Adding rxNorm drugs list to the jsonl

In [2]:
!pip install "spacy>=3.7.0,<3.8.0" "scispacy>=0.5.3,<0.6.0"
!pip install \
  https://s3-us-west-2.amazonaws.com/ai2-s2-scispacy/releases/v0.5.4/en_ner_bc5cdr_md-0.5.4.tar.gz

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.5/6.5 MB 225.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.2/14.2 MB 111.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 875.0/875.0 kB 147.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 172.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 865.0/865.0 kB 142.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.2/10.2 MB 147.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.0/18.0 MB 261.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.5/9.5 MB 267.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 35.7/35.7 MB 237.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 34/34 [scispacy]/34 [spacy]-learn]ainz]
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 119.8/119.8 MB 56.6 MB/s eta 0:00:0000:0100:01
  Preparing metadata (setup.py) ... done
  DEPRECATION: Building 'en_ner_bc5cdr_md' using the legacy setup.py

In [3]:
import importlib
import emailProcessor

# Reloading module so that new functions are picked up
importlib.reload(emailProcessor)

/opt/conda/lib/python3.12/site-packages/spacy/language.py:2195: FutureWarning: Possible set union at position 6328
  deserializers["tokenizer"] = lambda p: self.tokenizer.from_disk(  # type: ignore[union-attr]


<module 'emailProcessor' from '/home/jovyan/work/Group-3/emailProcessor.py'>

In [4]:
from emailProcessor import extractRXnormDrugs

input_file = 'output_data/json_with_crossRefs.jsonl'
output_file = 'output_data/json_with_crossRefs_rxnorm.jsonl'
extractor = extractRXnormDrugs(input_file,output_file)
extractor.add_rxnorm_drugs_name()

File saved successfully


[{'email_id': 'htcf0232',
  'output': '{\n  "@context": {\n    "@vocab": "https://schema.org/",\n    "email": "https://schema.org/EmailMessage",\n    "person": "https://schema.org/Person",\n    "org": "https://schema.org/Organization",\n    "document": "https://schema.org/DigitalDocument",\n    "topicEntity": "https://schema.org/Thing",\n    "url": "https://schema.org/URL",\n    "gpe": "https://schema.org/Place"\n  },\n  "@type": "case:Legislation",\n  "semantic_type": "Legal Communication Record",\n  "identifier": "Case-1996-Folio-PR-Thread",\n  "legalStatus": "Confidential document disclosed in litigation",\n  "dateFiled": "1996-09-04",\n  "language": [\n    "en"\n  ],\n  "confidentialityNotice": "HIGHLY CONFIDENTIAL - ACCESS RESTRICTED BY COURT ORDER IN COMMONWEALTH OF KENTUCKY, EX REL. JACK CONWAY, ATTORNEY GENERAL v. PURDUE",\n  "hasPart": {\n    "@type": "email:EmailMessage",\n    "semantic_type": "Email Communication",\n    "identifier": "Email-1996-09-04-0909-RS",\n    "subject

## Extracting additional semantic information using Qwen API

In [27]:
importlib.reload(emailProcessor)

<module 'emailProcessor' from '/home/jovyan/work/Group-3/emailProcessor.py'>

In [20]:
from dotenv import load_dotenv
import os

env_path = os.getcwd()+'/.env'
print(env_path)
load_dotenv(env_path)

/home/jovyan/work/Group-3/.env


True

In [30]:
from emailProcessor import QwenEntityExtractor

api_key2 = os.getenv('QWEN_API_KEY')
input_file = "output_data/json_with_crossRefs_rxnorm.jsonl"
extractor = QwenEntityExtractor(api_key=api_key2)
# split into batches
batch_files = extractor.split_into_batches(
    input_file=input_file,  
    output_dir="enriched_batches"  
)


Batch Planning:
   Total items: 652
   Items per batch: 10
   Total batches needed: 66

Created 66 batch files in 'enriched_batches/' directory



In [ ]:
# process each batch one by one
total_api_calls = 0
  for i in range(1,len(batch_files)+1):
    print(f'Processing batch {i:03d}\n')
    api_calls = extractor.process_batch(
        batch_file = f'{batch_dir}/batch_{i:03d}.json',
        output_file = f'{output_dir}/enriched_batch_{i:03d}.json'
    )
    total_api_calls += api_calls
    print(f'Api calls this batch: {api_calls}')
  print(f'Total api calls: {total_api_calls}\n')

In [ ]:
# find out and reprocess the failed batches
from emailProcessor import reprocessFailedBatch

reprocessor = reprocessFailedBatch(api_key2)
batch_dir = ""
enriched_batch_dir = ""
errors = reprocessor.find_error_inBatches(enriched_batch_dir)
print('Number of failed batches',len(errors))

if len(errors)>0:
    print('\nRe-processing failed batch')
    reprocessor.reprocess_failed_batches(batch_dir,enriched_batch_dir)

In [ ]:
# merge all the batches into single jsonl file
from emailProcessor import merge_batches_to_jsonl

enriched_batch = ''
op_path = ''

merged_items = merge_batches_to_jsonl(
    enriched_folder=enriched_batch,
    output_file=op_path
)

print(f"All {len(merged_items)} items merged to JSONL!")